In [1]:
using Plots;
using DelimitedFiles;
using AugmentedGaussianProcesses;

In [2]:
X = readdlm("data/banana_X_train");
Y = readdlm("data/banana_Y_train")[:];

In [3]:
# Run sparse classification with increasing number of inducing points
Ms = [4, 8, 16, 32, 64]
models = Vector{AbstractGP}(undef,length(Ms)+1)
kernel = RBFKernel(1.0)
for (index, num_inducing) in enumerate(Ms)
    m = SVGP(X, Y, kernel,LogisticLikelihood(),AnalyticVI(),num_inducing)
    println("Training with $(num_inducing) points")
    @time train!(m,iterations=20)
    models[index]=m;
end

Training with 4 points
  7.731405 seconds (35.43 M allocations: 1.838 GiB, 9.49% gc time)
Training with 8 points
  0.133731 seconds (502.64 k allocations: 152.414 MiB, 14.34% gc time)
Training with 16 points
  0.204259 seconds (502.64 k allocations: 252.077 MiB, 11.88% gc time)
Training with 32 points
  0.347815 seconds (502.64 k allocations: 452.411 MiB, 10.97% gc time)
Training with 64 points
  0.760047 seconds (502.99 k allocations: 857.149 MiB, 20.97% gc time)


In [4]:
mfull = VGP(X, Y, kernel,LogisticLikelihood(),AnalyticVI())
train!(mfull,iterations=5);
models[end] = mfull;

In [5]:
function compute_Grid(model,nGrid=50)
    mins = [-3.25,-2.85]
    maxs = [3.65,3.4]
    xlin = range(mins[1],stop=maxs[1],length=nGrid)
    ylin = range(mins[2],stop=maxs[2],length=nGrid)
    Xplot = hcat([j for i in xlin, j in ylin][:],[i for i in xlin, j in ylin][:])
    y =  proba_y(model,Xplot)
    return (y,xlin,ylin)
    end;

In [6]:
function plotdata(X,Y)
    Plots.plot(X[Y.==1,1],X[Y.==1,2],alpha=0.2,t=:scatter,markerstrokewidth=0.0,lab="",size=(300,500));
    Plots.plot!(X[Y.==-1,1],X[Y.==-1,2],alpha=0.2,t=:scatter,markerstrokewidth=0.0,lab="",size=(300,500));
end;

In [7]:
function plotcontour(model,X,Y)
    nGrid = 40
    (predic,x,y) = compute_Grid(model,nGrid);
    plotdata(X,Y)
    if in(:Z,fieldnames(typeof(model)))
        println("Plotting model with $(model.nFeatures) points")
        Plots.plot!(model.Z[1][:,1],model.Z[1][:,2],msize=2.0,color="black",t=:scatter,lab="")
    end
    return Plots.plot!(x,y,reshape(predic,nGrid,nGrid),cbar=false,t=:contour,levels=[0.5],fill=false,color=:black,linewidth=2.0,title=(in(:Z,fieldnames(typeof(model))) ? "M = $(model.nFeatures)" : "full"))
end;

In [8]:
Plots.plot(broadcast(x->plotcontour(x,X,Y),models)...,layout=(1,length(models)),size=(1000,200))

Plotting model with 4 points
Plotting model with 8 points
Plotting model with 16 points
Plotting model with 32 points
Plotting model with 64 points
